In [28]:
from dataclasses import dataclass
import sympy
import numpy as np
import pickle
import copy
from collections import deque
from sympy.utilities import lambdify
from tqdm import tqdm
import warnings




warnings.filterwarnings("error")
rng = np.random.default_rng()

# EXTRA_FUNC_DICT = {
#     'exp': make_function(np.exp, 'exp', 1),
#     'pow': make_function(np.power, 'pow', 2)
# }

#dict taken from the github of the benchmark
STR2SYMPY = {
    'neg': lambda x: -x,
    'abs': sympy.Abs,
    'sqrt': sympy.sqrt,
    'exp': sympy.exp,
    'log': sympy.log,
    'sin': sympy.sin,
    'cos': sympy.cos,
    'tan': sympy.tan,
    'add': lambda x, y : x + y,
    'sub': lambda x, y : x - y,
    'mul': lambda x, y : x * y,
    'div': lambda x, y : x / y,
    'pow': lambda x, y : x ** y
}

binary_functions=np.array(['add','sub','mul','div','pow'])
unary_functions=np.array(['neg','sqrt','exp','log','sin','cos','tan'])
#pi breaks things when converting to numpy here somehow
extra_constants=np.array(['2','3','4','5'])#,'pi'])
true_variables=(['x0','x1','x2','x3','x4','x5'])

@dataclass
class ExpNode:
    kind: str
    num_children: int
    children: list
    parent: 'ExpNode' = None

def find_depth(node: ExpNode,currdepth):
    if isinstance(node, np.ndarray):
        return currdepth
    elif node.num_children==1:
        return find_depth(node.children[0],currdepth+1)
    else:
        return max(find_depth(node.children[0],currdepth+1),find_depth(node.children[1],currdepth+1))

def find_variables(root: ExpNode):
    if isinstance(root, np.ndarray):
        return root
    dir=rng.uniform(0,1)
    if dir<1/2 or root.num_children==1:
        return find_variables(root.children[0])
    elif dir>1/2 and root.num_children>1:
        return find_variables(root.children[1])


def visit(formula: ExpNode):
    tovisit=deque()
    tovisit.append((formula,None,0))
    count=0
    while tovisit:
        node,parent,j=tovisit.popleft()
        if not isinstance(node, np.ndarray):
            for i,child in enumerate(node.children):
                tovisit.append((child,node,i))
        count+=1
        if rng.integers(1,count+1)==count:
            item=node
            itemparent=parent
            itemid=j
    return item,itemparent,itemid

def cut_and_shorten(formula: ExpNode):
    cutpoint,cutparent,cutid=visit(formula)
    if cutparent is not None:
        cutparent.children[cutid]=find_variables(cutpoint)
    return formula

def cut_and_regenerate(formula: ExpNode, variables,dummy,simplified):
    cutpoint,cutparent,cutid=visit(formula)
    if cutparent is not None:
        cutparent.children[cutid]=generate_Expression(variables,dummy,simplified)
        cutparent.children[cutid].parent=cutparent
    else:
        formula=generate_Expression(variables,dummy,simplified)
    return formula

def crossover(formula1: ExpNode,formula2: ExpNode):
    cxpoint1,parent1,id1=visit(formula1)
    cxpoint2,parent2,id2=visit(formula2)
    if (parent1 is None) and (not isinstance(cxpoint2,np.ndarray)):
        return cxpoint2
    elif (parent1 is not None) and (not isinstance(cxpoint2,np.ndarray)):
        cxpoint2.parent=parent1
        parent1.children[id1]=cxpoint2
        return formula1
    elif parent1 is not None:
        parent1.children[id1]=cxpoint2
        return formula1
    else:
        return formula1



def choose_function():
    fn_choice=rng.uniform(0,1)
    children=0
    if fn_choice>7/12:
        kind=rng.choice(binary_functions,1)
        children=2
    else:
        kind=rng.choice(unary_functions,1)
        children=1
    return kind[0],children

def generate_subtree(root,depth,max_depth,variables):
    if depth==max_depth:
        for n in range(root.num_children):
            var=rng.choice(variables,1)
            # if var[0]=='const':
            root.children.append(var)
    else:
        for n in range(root.num_children):
            fn,children=choose_function()
            child=ExpNode(fn,children,[],root)
            generate_subtree(child,depth+1,max_depth,variables)
            root.children.append(child)


def generate_Expression(variables: np.ndarray,dummy=True,simplified=False):
    depth=rng.integers(1,3)
    num_variables=rng.integers(1,variables.shape[0]+1)
    #check if replacement mayu be usefull (the same variable is used twice in different fragments of the expression)
    # we may choose just one variable then
    if dummy:
        used_variables=rng.choice(variables,num_variables,replace=False)
    else:
        used_variables=variables
    #print(num_variables,used_variables)
    #using uniform generation
    d=0
    curr_fn,kids=choose_function()
    root=ExpNode(curr_fn,kids,[])
    if simplified:
        generate_subtree(root,1,depth,used_variables)
    else:
        generate_subtree(root,1,depth,np.concatenate([used_variables,extra_constants]))
    return root

        
# def parse_Expression(expr: ExpNode):
#     if type(expr)==np.ndarray:
#         return sympy.symbols(expr[0])
#     else:
#         print(expr.kind)
#         print((parse_Expression(expr.children[i]) for i in range(expr.num_children)))
#         return STR2SYMPY[expr.kind](parse_Expression(expr.children[i]) for i in range(expr.num_children))

def parse_Expression(expr: ExpNode):
    if isinstance(expr, np.ndarray):
        return sympy.symbols(expr[0])
    elif expr.kind in STR2SYMPY:
        # Parse children recursively
        parsed_children = [parse_Expression(child) for child in expr.children]
        if expr.kind == 'div' and len(parsed_children) == 2:
            # Check for division by zero
            denominator = parsed_children[1]
            if denominator == 0:
                raise ZeroDivisionError(f"Division by zero detected in expression: {expr}")
        # Apply the corresponding sympy function/operator
        return STR2SYMPY[expr.kind](*parsed_children)
    else:
        raise ValueError(f"Unsupported expression kind: {expr.kind}")
    

    


In [31]:
class SGA:
    def __init__(self,pop_size,children_size,crossover_prob,mutation_prob,num_iter,variables,data,dummy=False,simplified=False):
        self.pop_size=pop_size
        self.crossover_prob=crossover_prob
        self.mutation_prob=mutation_prob
        self.num_iter=num_iter
        self.variables=variables
        #self.objective_function=objective_function
        self.dummy=dummy
        self.data=data
        self.children_size=children_size
        self.simplified=simplified

    def initial_population(self):
        self.parent_population=[generate_Expression(self.variables,self.dummy,self.simplified) for i in range(self.pop_size)]
        self.best_individual=self.parent_population[0]
        #a litt;e shenanigans
        print('pop_created')
        self.best_objective_value = min([self.objective_function(pop,self.data) for pop in self.parent_population])
    
    def objective_function(self,expression,data):

        try:
            parsed_expression=parse_Expression(expression)
        except:
            return np.inf
        
        variables=[_ for _ in parsed_expression.atoms() if type(_) is sympy.Symbol and str(_) in true_variables]
        nums=[int(str(_)[1]) for _ in variables]
        #print(parsed_expression,nums)
        try:
            fn=lambdify(variables,parsed_expression,'numpy')
            if len(nums)==0:
                return np.inf
            
            input=tuple([data[:,num] for num in nums])
            #print(parsed_expression)
            #print(input)
            res=fn(*input)
            #print(type(res))
            score=np.sum(np.sqrt((res-data[:,[data.shape[1]-1]])*(res-data[:,[data.shape[1]-1]])))
            depth=find_depth(expression,0)
            #print(score)
            if depth>3*data.shape[1]:
                score=score*depth
            if len(nums)<data.shape[1] and self.dummy==False:
                return (data.shape[1]-len(nums))*score
            else:
                return score
        except RuntimeWarning:
            print('sym runtime')
            return np.inf
        except KeyError:
            print('strange')
            return np.inf

    def fit(self):
        for t in tqdm(range(self.num_iter)):
            self.children_population=[]
            
            for i in range(self.pop_size-1):
                if rng.uniform(0,1)<self.crossover_prob:
                    #check here if copy is deep enough
                    self.children_population.append(crossover(copy.deepcopy(self.parent_population[i]),copy.deepcopy(self.parent_population[i+1])))
                else:
                    self.children_population.append(self.parent_population[i])
            #print(len(self.children_population))

            for i in range(self.children_size-1):
                if rng.uniform(0,1)<self.mutation_prob:
                    self.children_population[i]=cut_and_regenerate(self.children_population[i],self.variables,self.dummy,self.simplified)
                elif rng.uniform(0,1)<self.mutation_prob:
                    self.children_population[i]=cut_and_shorten(self.children_population[i])
                    
            total_pop=self.parent_population+self.children_population
            self.fitness_values=[self.objective_function(pop,self.data) for pop in total_pop]
            self.parent_population=[x for _, x in sorted(zip(self.fitness_values, total_pop), key=lambda pair: pair[0])][:self.pop_size]

            if min(self.fitness_values)<self.best_objective_value:
                self.best_objective_value=min(self.fitness_values)
                self.best_individual=self.parent_population[0]
            
            print(parse_Expression(self.best_individual),self.best_objective_value)
            #print([parse_Expression(pop,)])
            sample=[]
            for i in range(10):
                try:
                    sample.append(parse_Expression(self.parent_population[i]))
                except:
                    print('div by 0')
            print(sample)

        return parse_Expression(self.best_individual)


In [30]:
with open('srsd/medium_set/true_eq/feynman-i.8.14.pkl','rb') as eq:
    equaion=pickle.load(eq)
    print(equaion,type(equaion))

arr=np.loadtxt('srsd/medium_set/test/feynman-i.8.14.txt')
print(arr)
testing=SGA(100,100,0.95,0.3,100,np.array(['x0','x1','x2','x3']),arr,dummy=False)
print('initialized')
testing.initial_population()

testing.fit()

sqrt((x0 - x1)**2 + (x2 - x3)**2) <class 'sympy.core.power.Pow'>
[[ 2.00293401  0.76615789 -1.16301986 -2.29924894  1.67947364]
 [-0.1516021  -0.315528    4.28046425 -0.16175568  4.44524347]
 [ 7.22516759 -0.60686739  5.98877255 -2.48898992 11.54180351]
 ...
 [-0.38752721 -3.80981155 -4.00705763 -9.805081    6.73268929]
 [ 0.15153997  1.39060106 -0.13542526 -5.74073294  5.74062249]
 [-3.96895032 -3.69390316  2.53040955 -1.05597386  3.59691491]]
initialized
pop_created
4 + x3
<class 'numpy.ndarray'>
3938038.7484780285
exp(x3)
<class 'numpy.ndarray'>
300445319.95167243
sqrt(x3) - log(x2)
sym runtime
log(4**x0)
<class 'numpy.ndarray'>
6604057.952316344
cos(3*x1)
<class 'numpy.ndarray'>
5509106.115088513
cos(x2**2)
<class 'numpy.ndarray'>
5277290.968769724
2*x1
<class 'numpy.ndarray'>
7367821.937689007
3 - x0
<class 'numpy.ndarray'>
4208030.112891906
2/x0
<class 'numpy.ndarray'>
7477219.133289623
2*x2
<class 'numpy.ndarray'>
7547266.83743338
4 - x0
<class 'numpy.ndarray'>
3917479.072419799

  0%|          | 0/100 [00:00<?, ?it/s]

4 + x3
<class 'numpy.ndarray'>
3938038.7484780285
exp(x3)
<class 'numpy.ndarray'>
300445319.95167243
sqrt(x3) - log(x2)
sym runtime
log(4**x0)
<class 'numpy.ndarray'>
6604057.952316344
cos(3*x1)
<class 'numpy.ndarray'>
5509106.115088513
cos(x2**2)
<class 'numpy.ndarray'>
5277290.968769724
2*x1
<class 'numpy.ndarray'>
7367821.937689007
3 - x0
<class 'numpy.ndarray'>
4208030.112891906
2/x0
<class 'numpy.ndarray'>
7477219.133289623
2*x2
<class 'numpy.ndarray'>
7547266.83743338
4 - x0
<class 'numpy.ndarray'>
3917479.072419799
exp(tan(x1))
<class 'numpy.ndarray'>
2.3637415472630105e+62
sqrt(4 + x3)
sym runtime
x0 + x1
<class 'numpy.ndarray'>
6558305.447869224
-x2
<class 'numpy.ndarray'>
6156778.987446821
sqrt(x0)*sqrt(x2)
sym runtime
x3**2
<class 'numpy.ndarray'>
12373396.608948894
-3**x0
<class 'numpy.ndarray'>
499008504.262908
2*x0
<class 'numpy.ndarray'>
7484186.786473345
-2 + exp(x3)
<class 'numpy.ndarray'>
301572604.8759724
sin(x2)/tan(x1)
<class 'numpy.ndarray'>
7013472.852743819
sqrt

  1%|          | 1/100 [00:00<00:48,  2.04it/s]

<class 'numpy.ndarray'>
5558076.135333498
sin(x2)
<class 'numpy.ndarray'>
5653652.105499788
log(x2)
sym runtime
4*x3
<class 'numpy.ndarray'>
10876743.289598882
log(x0)
sym runtime
x0 - x1
<class 'numpy.ndarray'>
6630663.782249836
sqrt(3 + x0)
sym runtime
tan(x3)
<class 'numpy.ndarray'>
10510686.618677527
exp(x0)
<class 'numpy.ndarray'>
213785550.14018735
sqrt(2 + x0)
sym runtime
2 - x3
<class 'numpy.ndarray'>
4829894.632748489
5 + x2 + sin(2) + sin(x2)
<class 'numpy.ndarray'>
3982269.93309871
2 + 4 - x2 + tan(4)
<class 'numpy.ndarray'>
4130197.079877225
2 - x3
<class 'numpy.ndarray'>
4829894.632748489
2 + sin(x2)
<class 'numpy.ndarray'>
3948114.8590152003
exp(exp(x1)**4)
sym runtime
cos(x1)
<class 'numpy.ndarray'>
5328294.332935086
sqrt(x0)
sym runtime
4/2 14143636.479082357
[2 + 4 - x2 + x3, 5 - x2, 4 - x0, 4 - x0, 4 + x3, 2 + sin(x2), 5 + x2 + sin(2) + sin(x2), 2 + 4 - x2 + tan(4), sin(x0 + x0**2*(5 - x3)), 3 - x0]
2 + 4 - x2 + x3
<class 'numpy.ndarray'>
4714545.493027452
5 - x2
<cla

...

 99%|█████████▉| 99/100 [02:31<00:01,  1.57s/it]

<class 'numpy.ndarray'>
3019763.0828326046
2*3 - sin(sqrt(5) + sin(sqrt(5) + log(5) + sin(x0 + x1 + x2 - x3**5 + sin(x2) + tan(x1))))
<class 'numpy.ndarray'>
2899752.0777825993
2*3 - sin(sqrt(5) + sin(3 + sqrt(5) + sin(x0 + log(5)) + sin(cos(log(5)))))
<class 'numpy.ndarray'>
2898459.872430942
-x0*tan(x0)
<class 'numpy.ndarray'>
42375058.05864237
2*3 - sin(sqrt(5) + sin(3 + sqrt(5) + sin(-x3**5 + log(x1)/sin(x1) + sin(cos(log(5))) + tan(x1)) + sin(cos(log(5)))))
sym runtime
2*3 - sin(sqrt(5) + sin(3 + 4**x0 + sqrt(5) + sin(cos(log(5)))))
<class 'numpy.ndarray'>
2911747.691547584
3 - x3**5 - sin(3) - sin(sqrt(5) + sin(3 + sqrt(5) + sin(x0 + x1 + x2 - x3**5 + sin(x2) + tan(x1)) + sin(cos(log(5))))) + tan(x1)
<class 'numpy.ndarray'>
4721487793.311195
2*3 + sin(3) - sin(sqrt(5) + sin(3 + sqrt(5) + sin(x0 + x1 + x2 - x3**5 + sin(x2) + tan(x1)) + sin(cos(log(5))))) - sin(sin(cos(log(5))))
<class 'numpy.ndarray'>
2899773.4201276423
sin(3) + sin(sqrt(5) + sin(3 + sqrt(5) + sin(2*5 + x0 + x1 + 

100%|██████████| 100/100 [02:33<00:00,  1.53s/it]

2907213.3929187073
2*3 - sin(3) - sin(sqrt(5) + sin(sqrt(4) + sqrt(5) + sin(5 + x0 + x1 + x2 - (x3**5)**5 + cos(2)))) + sin(sin(3))
<class 'numpy.ndarray'>
2898571.8830836606
2*3 - sin(sin(sqrt(2 + 4) + sin(sqrt(4)) + sin(x0 + x1 + x2 - x3**5 + sin(x0) + tan(x1)) + sin(cos(log((2 + 4)/5)))) + (2 + 4)/3) 2898383.894941505
[2*3 - sin(sin(sqrt(2 + 4) + sin(sqrt(4)) + sin(x0 + x1 + x2 - x3**5 + sin(x0) + tan(x1)) + sin(cos(log((2 + 4)/5)))) + (2 + 4)/3), 2*3 - sin(sin(sqrt(2 + 4) + sin(sqrt(4)) + sin(x0 + x1 + x2 - x3**5 + sin(x0) + tan(x1)) + sin(cos(log((2 + 4)/5)))) + (2 + 4)/3), 2*3 - sin(sin(sqrt(5) + sin(sqrt(4)) + sin(x1 + x2 - x3**5 + sin(sqrt(4)) + sin(x0) + tan(x1)) + sin(cos(sin(3)))) + (2 + 4)/3), 2*3 - sin(sin(sqrt(5) + sin(sqrt(4)) + sin(x1 + x2 - x3**5 + sin(sqrt(4)) + sin(x0) + tan(x1)) + sin(cos(sin(3)))) + (2 + 4)/3), 2*3 - sin(sin(sqrt(5) + sin(sqrt(4)) + sin(x1 + x2 - x3**5 + sin(sqrt(4)) + sin(x0) + tan(x1)) + sin(cos(sin(3)))) + (2 + 4)/3), 2*3 - sin(2 + sin(sqrt(5) +

2*3 - sin(sin(sqrt(2 + 4) + sin(sqrt(4)) + sin(x0 + x1 + x2 - x3**5 + sin(x0) + tan(x1)) + sin(cos(log((2 + 4)/5)))) + (2 + 4)/3)

In [32]:
with open('srsd/medium_set/true_eq/feynman-i.8.14.pkl','rb') as eq:
    equaion=pickle.load(eq)
    print(equaion,type(equaion))

arr=np.loadtxt('srsd/medium_set/test/feynman-i.8.14.txt')
print(arr)
testing=SGA(100,100,0.95,0.3,100,np.array(['x0','x1','x2','x3']),arr,dummy=False)
print('initialized')
testing.initial_population()

testing.fit()

sqrt((x0 - x1)**2 + (x2 - x3)**2) <class 'sympy.core.power.Pow'>
[[ 2.00293401  0.76615789 -1.16301986 -2.29924894  1.67947364]
 [-0.1516021  -0.315528    4.28046425 -0.16175568  4.44524347]
 [ 7.22516759 -0.60686739  5.98877255 -2.48898992 11.54180351]
 ...
 [-0.38752721 -3.80981155 -4.00705763 -9.805081    6.73268929]
 [ 0.15153997  1.39060106 -0.13542526 -5.74073294  5.74062249]
 [-3.96895032 -3.69390316  2.53040955 -1.05597386  3.59691491]]
initialized
pop_created
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime


  0%|          | 0/100 [00:00<?, ?it/s]

sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime


  1%|          | 1/100 [00:00<00:39,  2.50it/s]

sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
-(-5 + x2)/tan(4) 14895933.701184034
[-(-5 + x2)/tan(4), exp(cos(x1)), (x0 + x2)*exp(-3), sin(x2*x3), 3 + x2, x2*sin(x1), -(-5 + x2)/4, 2**(x2/4), 2**(x2/4), 2 - x0]
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime


...

 99%|█████████▉| 99/100 [02:22<00:01,  1.58s/it]

4 - sin(5) - sin(cos(4*cos(x0*(-3**x2 + 4/x1)*sin(exp(-exp(4))*cos(sin(x3))))/cos(cos(5)))/4) 2897967.7504716786
[4 - sin(5) - sin(cos(4*cos(x0*(-3**x2 + 4/x1)*sin(exp(-exp(4))*cos(sin(x3))))/cos(cos(5)))/4), 4 - sin(5) - sin(cos(4*cos(x0*(-3**x2 + 4/x1)*sin(exp(-exp(4))*cos(sin(x3))))/cos(cos(5)))/4), 4 - sin(cos(4*cos(4*(x0 - sin(x3))*(x3/(x0 + 2*x2 - 2*x3) - sin(x0))*sin(sin(exp(-4)*cos(2*2 - x1/x2))))/cos(cos((4 + 5)/(2*3))))/4) - sin(exp(4)), 4 - sin(cos(4*cos(4*(x0 - sin(x3))*(x3/(x0 + 2*x2 - 2*x3) - sin(x0))*sin(sin(exp(-4)*cos(4 - x1/x2))))/cos(cos((4 + 5)/(2*3))))/4) - sin(exp(4)), 4 - sin(cos(4*cos((4 + cos(2*2 - exp(4/x1))/4)*(x0 - sin(x3))*(x3/(x0 + 2*x2 - 2*x3) - sin(x0))*sin(sin(exp(-4)*cos(2*2 - x1/x2))))/cos(cos((4 + 5)/(2*3))))/4) - sin(exp(4)), 4 - sin(cos(4*cos((1 - sin(x0))*(4 + cos(2*2 - x1/x2)/4)*(x0 - sin(x3))*sin(sin(exp(-4)*cos(2*2 - x1/x2))))/cos(cos((4 + 5)/(2*3))))/4) - sin(exp(4)), 4 - sin(cos(4*cos((4 + cos(2*2 - x1/x2)/4)*(x0 - sin(x3))*(x3/(x0 + 2*x2 - 2

100%|██████████| 100/100 [02:24<00:00,  1.44s/it]

4 - sin(5) - sin(cos(2*4/3)/4) 2897967.7504716786
[4 - sin(5) - sin(cos(4*cos(x0*(-3**x2 + 4/x1)*sin(exp(-exp(4))*cos(sin(x3))))/cos(cos(5)))/4), 4 - sin(cos(4*cos(4*(x0 - sin(x3))*(x3/(x0 + 2*x2 - 2*x3) - sin(x0))*sin(sin(exp(-4)*cos(2*2 - x1/x2))))/cos(cos((4 + 5)/(2*3))))/4) - sin(exp(4)), 4 - sin(cos(4*cos(4*(x0 - sin(x3))*(x3/(x0 + 2*x2 - 2*x3) - sin(x0))*sin(sin(exp(-4)*cos(4 - x1/x2))))/cos(cos((4 + 5)/(2*3))))/4) - sin(exp(4)), 4 - sin(cos(4*cos((4 + cos(2*2 - exp(4/x1))/4)*(x0 - sin(x3))*(x3/(x0 + 2*x2 - 2*x3) - sin(x0))*sin(sin(exp(-4)*cos(2*2 - x1/x2))))/cos(cos((4 + 5)/(2*3))))/4) - sin(exp(4)), 4 - sin(cos(4*cos((1 - sin(x0))*(4 + cos(2*2 - x1/x2)/4)*(x0 - sin(x3))*sin(sin(exp(-4)*cos(2*2 - x1/x2))))/cos(cos((4 + 5)/(2*3))))/4) - sin(exp(4)), 4 - sin(cos(4*cos((1 - sin(x0))*(4 + cos(2 + 4 - x1/x2)/4)*(x0 - sin(x3))*sin(sin(exp(-4)*cos(2*2 - x1/x2))))/cos(cos((4 + 5)/(2*3))))/4) - sin(exp(4)), 4 - sin(cos(4*cos((4 + cos(2*2 - x1/x2)/4)*(x0 - sin(x3))*(x3/(x0 + 2*x2 - 2*x3) 

4 - sin(5) - sin(cos(2*4/3)/4)

In [33]:
# with open('srsd/medium_set/true_eq/feynman-i.8.14.pkl','rb') as eq:
#     equaion=pickle.load(eq)
#     print(equaion,type(equaion))

# arr=np.loadtxt('srsd/medium_set/test/feynman-i.8.14.txt')
# print(arr)
# arr1=np.loadtxt('srsd/medium_set/test/feynman-i.34.8.txt')
# print(arr1)

#dummy variable amounts disagree with dataset decription
data=np.loadtxt('srsd/easy_set_dummy/train/feynman-i.12.5.txt')
print(data.shape)
with open('srsd/easy_set_dummy/true_eq/feynman-i.12.5.pkl','rb') as eq:
    equaion=pickle.load(eq)
    print(equaion,type(equaion))

testing=SGA(100,100,0.95,0.3,100,np.array(['x0','x1','x2','x3']),arr,dummy=True,simplified=True)
print('initialized')
testing.initial_population()

testing.fit()

(8000, 5)
x2*x3 <class 'sympy.core.mul.Mul'>
initialized
pop_created
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime


  0%|          | 0/100 [00:00<?, ?it/s]

sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime


  1%|          | 1/100 [00:00<00:57,  1.73it/s]

sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
cos(cos(cos(x2))) 4932664.003519647
[cos(cos(cos(x2))), sin(cos(cos(x0))), tan(cos(x2**2)), cos(tan(x3/x0)), exp(cos(x0))*cos(x2), cos(x0), cos(x0), sin(exp(x2)), cos(x3), cos(x3)]
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime
sym runtime


...

 99%|█████████▉| 99/100 [01:38<00:01,  1.05s/it]

sym runtime
sym runtime
sym runtime
exp(cos(cos(exp(cos(cos(cos(cos(sin(cos(cos(cos(x0))))))))))))*exp(cos(cos(cos(cos(cos(cos(cos(cos(cos(x0)))))))))) 2898010.253110525
[exp(cos(cos(exp(cos(cos(cos(cos(sin(cos(cos(cos(x0))))))))))))*exp(cos(cos(cos(cos(cos(cos(cos(cos(cos(x0)))))))))), exp(cos(cos(exp(cos(cos(cos(cos(sin(cos(cos(cos(tan(x0)))))))))))))*exp(cos(cos(cos(cos(cos(cos(cos(cos(cos(tan(x0))))))))))), exp(cos(cos(exp(cos(cos(cos(cos(sin(cos(cos(cos(tan(x0)))))))))))))*exp(cos(cos(cos(cos(cos(cos(cos(cos(cos(tan(x0))))))))))), exp(cos(cos(exp(cos(cos(cos(cos(sin(cos(cos(cos(tan(x0)))))))))))))*exp(cos(cos(cos(cos(cos(cos(cos(cos(cos(tan(x0))))))))))), exp(cos(cos(exp(cos(cos(cos(cos(sin(cos(cos(cos(tan(x0)))))))))))))*exp(cos(cos(cos(cos(cos(cos(cos(cos(cos(tan(x0))))))))))), exp(cos(cos(exp(cos(cos(cos(cos(sin(cos(cos(x0)))))))))))*exp(cos(cos(cos(cos(cos(cos(cos(cos(x0))))))))), exp(cos(cos(exp(cos(cos(cos(cos(sin(cos(cos(x0)))))))))))*exp(cos(cos(cos(cos(cos(cos(cos(cos(x0)

100%|██████████| 100/100 [01:39<00:00,  1.00it/s]

sym runtime
sym runtime
exp(cos(cos(exp(cos(cos(cos(cos(sin(cos(cos(cos(x0))))))))))))*exp(cos(cos(cos(cos(cos(cos(cos(cos(cos(x0)))))))))) 2898010.253110525
[exp(cos(cos(exp(cos(cos(cos(cos(sin(cos(cos(cos(x0))))))))))))*exp(cos(cos(cos(cos(cos(cos(cos(cos(cos(x0)))))))))), exp(cos(cos(exp(cos(cos(cos(cos(sin(cos(cos(cos(tan(x0)))))))))))))*exp(cos(cos(cos(cos(cos(cos(cos(cos(cos(tan(x0))))))))))), exp(cos(cos(exp(cos(cos(cos(cos(sin(cos(cos(cos(tan(x0)))))))))))))*exp(cos(cos(cos(cos(cos(cos(cos(cos(cos(tan(x0))))))))))), exp(cos(cos(exp(cos(cos(cos(cos(sin(cos(cos(cos(tan(x0)))))))))))))*exp(cos(cos(cos(cos(cos(cos(cos(cos(cos(tan(x0))))))))))), exp(cos(cos(exp(cos(cos(cos(cos(sin(cos(cos(cos(tan(x0)))))))))))))*exp(cos(cos(cos(cos(cos(cos(cos(cos(cos(tan(x0))))))))))), exp(cos(cos(exp(cos(cos(cos(cos(sin(cos(cos(x0)))))))))))*exp(cos(cos(cos(cos(cos(cos(cos(cos(x0))))))))), exp(cos(cos(exp(cos(cos(cos(cos(sin(cos(cos(x0)))))))))))*exp(cos(cos(cos(cos(cos(cos(cos(cos(x0))))))))), ex

exp(cos(cos(exp(cos(cos(cos(cos(sin(cos(cos(cos(x0))))))))))))*exp(cos(cos(cos(cos(cos(cos(cos(cos(cos(x0))))))))))

In [25]:
# Define the symbolic variable
x3 = sympy.Symbol('x3')

# Define the symbolic expression, replacing pi with sp.pi
expression = -sympy.pi + x3 + sympy.exp(sympy.pi)
fn=lambdify([sympy.Symbol('x3')],expression,'numpy')
tupla=(np.array([-2.29924894, -0.16175568, -2.48898992,  0.11894908, -8.50794173,
       -5.41838146, -1.82835838,  0.2282993 ,  5.64902424, -2.65844095,
       -0.18728225,  0.26656019, -2.77333153,  0.79655389,  6.99942364,
        7.07346213, -1.61494835,  4.40465745,  0.25336077, -0.89129753,
        0.27187765,  0.69642027,  0.17362863,  2.24225245, -0.72077347,
       -2.10908807, -4.28975521,  2.94324571, -0.40634918, -2.34628313,
       -0.70787444,  0.14648986, -3.28608142,  4.81295499,  3.00120162,
       -1.32091774,  0.49377602,  5.76689146,  1.54535385,  7.68142202,
        0.13663641,  0.29298528,  8.13730145, -1.34287545,  0.16347124,
       -0.7489493 ,  0.46944761, -0.26962757, -4.30415169, -2.03019333,
        0.21035755, -1.90063313, -2.89876326, -0.96964696, -0.65451313,
        8.83022878, -5.8708818 ,  1.12638345, -2.1371395 ,  4.48406938,
       -0.12041674,  1.22995601, -1.32620879, -0.20793985,  1.28942515,
       -8.32619839, -0.68098606, -0.69396448,  1.88570987, -2.03144054,
       -0.88200878, -0.27686401,  0.89265364,  0.35549856,  4.89583422,
        1.52821263,  8.8274567 , -0.6844199 ,  0.15279267, -0.82629552,
        0.28345739, -2.23651683,  0.13955077, -5.17376382, -5.74409437,
       -0.116734  ,  0.19620189,  0.19487543, -0.10140859,  4.09259761,
        2.0784587 ,  3.47598633, -0.14593976, -0.12308522,  1.3027908 ,
       -0.67701334,  4.80137616, -0.19130059,  4.89081289, -0.33977659,
        4.85366499,  0.15931611,  0.10192371,  6.92885379, -1.16035721,
        7.05620226, -4.68538933,  0.20819338, -0.96475832, -5.44592788,
       -0.43237175, -0.21904206,  0.35449264,  2.53571002,  0.11689397,
        1.74817891,  0.61233576, -0.35599673,  4.39468562, -0.13657761,
       -0.55827228,  0.1938355 , -0.13099959,  1.04902002, -7.24599001,
        2.23407929, -2.28738137,  0.76392514, -6.54741973, -0.1110519 ,
       -7.72846066, -0.2930737 , -5.46964636,  0.17759982,  2.29525286,
        0.24032911, -1.67774744,  0.15405434,  3.0785473 , -0.68421775,
        0.35900978, -0.38580707, -2.17183512,  0.8526151 , -0.28663691,
        0.97767577, -0.43143272,  7.0904673 ,  2.41962031, -0.55309089,
       -0.93365706,  0.44428866,  1.00702662,  1.08385636,  1.16052657,
        0.71390863,  0.17459904,  0.43652075, -0.90169352, -2.08583946,
        0.18135131, -1.21064804, -0.30179712, -0.2688458 , -0.10019504,
        1.6846572 ,  0.30947731, -7.25539982,  0.18847587,  0.41940982,
        0.58326628,  9.66175445, -0.36807392,  3.15949204, -1.76464464,
        2.4836555 , -0.1129681 ,  0.40561008, -0.75410821,  4.09238679,
        0.21375265,  4.78832969, -0.13078243, -0.24724062, -1.62942171,
       -1.22892742, -9.1834364 ,  0.1673261 , -0.72537072,  0.87739825,
       -0.60093523, -1.25705738, -1.85572587, -0.1548408 , -1.38357353,
       -8.94490488,  0.86498337,  0.87663441,  0.7079651 , -1.59615367,
       -4.75634193, -6.73895454, -0.50937775, -2.45186962, -0.21221766,
        0.5625962 ,  0.71841042,  0.36246641,  0.53554331, -0.57833704,
        0.54439321, -1.05279568, -0.45234993,  0.94765666,  8.93723508,
       -0.16194822,  0.84473501,  2.47825102,  5.45179962,  0.13968322,
       -0.62592533,  3.78548497, -0.42678169,  5.08256265, -2.01348916,
        1.10823594, -8.04829531,  3.49182106, -8.31909481,  0.13364488,
       -1.61427904,  3.06267195,  0.92780855, -7.83283044,  0.21179881,
        0.33708498, -1.40919753, -2.87534285, -5.21631081,  0.1609982 ,
        0.15956439,  1.05911989, -0.27372823, -1.18486134,  7.83600375,
        4.58905891, -5.11780383,  3.12581498,  6.40767946, -9.18647535,
        1.87759159, -0.60340141,  2.6648508 , -7.02210315,  0.12605437,
        8.60215495,  0.36516303, -0.47847043, -5.8489727 , -0.18211964,
        6.89337813, -0.15096793,  0.9121181 ,  0.12597564, -1.19980734,
        0.17990549, -0.24915318, -0.15718326,  5.8886819 , -0.37216186,
       -3.37499022,  7.69149963,  2.89047306,  0.20238659,  4.30087863,
        0.72855029,  4.53792019,  9.18160513,  0.42156528, -0.40398138,
        3.43793522,  0.13350404, -5.70233577,  1.28598879,  3.17360923,
       -3.89644244, -2.20415655,  0.89621887,  0.7574408 , -0.20592907,
       -0.3814876 , -0.85981603,  4.91034861, -0.73030916, -7.99882321,
        3.45924177,  3.22349581, -8.26160628, -0.73609036, -2.13550156,
        0.14774294,  0.17385363,  0.12070709,  0.12973386,  1.42776609,
        0.36564654,  4.38634449,  6.59841996,  0.23819559, -2.3643878 ,
        0.22690475,  0.47184579,  1.17484487, -1.21094547, -3.02665453,
        0.50594489,  1.79832447, -0.39630695,  5.97329754, -0.46459994,
        6.33936781,  0.27196486,  8.01960204, -6.34582781, -0.14128048,
       -0.29686482, -1.98907619, -0.64340179,  1.56361339,  5.11828478,
        3.05002097, -0.58504097,  1.14616455,  0.14780515, -0.6588441 ,
       -0.16800115,  0.17998274,  5.05841269,  0.22741304, -5.87466944,
        1.64354121,  0.55585505,  3.15755341,  0.16628332,  3.60759545,
       -0.17046006,  1.12789617,  4.30869499, -0.21857486,  1.81685444,
        0.14971099,  0.27784304, -0.12618348,  4.86779086,  0.22263241,
        1.24567586,  0.12064434, -0.23695198, -0.1860931 ,  0.20606086,
        0.48136057, -0.66704592, -0.12795329, -0.10054397,  9.64002566,
       -1.79964212, -3.56092923, -0.77151368,  1.02937737, -3.97039983,
       -0.12541162,  0.16984374, -0.14927134, -7.23102333, -4.29375048,
        0.90417284,  0.22215235, -1.94556195, -0.12990395, -0.13366056,
        0.11303106,  0.14705609,  0.10959378,  4.23600264,  0.21967492,
       -5.39344139, -1.78112874, -4.96940445,  7.15794437,  0.78591171,
       -2.97054233, -2.950856  ,  5.90890492,  2.73208079,  0.50604145,
        0.15522101,  0.16629902,  0.14623307, -0.86479971,  2.05363388,
       -0.28368395,  0.44209336, -7.25811603, -0.36694747,  1.82524152,
        5.54327114,  5.23302362, -1.89060195, -0.1653353 ,  1.99794401,
       -1.36586626,  0.13159261,  0.63837352,  1.29649031,  0.18624857,
       -4.84017991, -0.68384347, -1.14020312, -0.31510866, -3.11900704,
       -1.06837387, -8.48754752, -2.17280884,  0.67496454, -9.46284702,
       -0.65190831,  3.11919076,  3.77516317,  5.7552704 ,  0.13882065,
        9.33648009,  0.2371027 ,  4.03984869,  4.22925876,  2.01129894,
       -0.17117629,  0.37054677, -0.19871048,  3.00452939,  0.33342585,
        0.13915725,  1.63718212, -1.65539855, -0.1725404 ,  3.61980987,
        6.87674627,  5.56661925, -9.81390286, -6.88804468, -0.18582852,
       -9.28551483,  4.20475   ,  0.31673608, -0.21071843,  0.98829249,
        0.17550603,  5.05343597, -8.96140711, -1.75636935,  1.70268785,
        6.55274536, -4.06078926,  0.55634203,  0.21344615, -1.89481799,
       -0.23220637,  2.72981433,  1.47148966, -0.60782325,  0.86784532,
       -2.08258145, -4.39037786, -0.87737363, -0.39984164,  0.90958285,
        5.14860312, -9.44790952, -2.33339455,  0.38738028,  0.75954133,
        0.24779733,  0.54522002, -0.96530502, -0.52402291, -0.54124468,
        0.49439764,  2.76253464,  0.10586212, -1.18020432,  0.12367937,
       -1.51207318,  2.11688981,  0.16078849,  0.83443388,  0.1156166 ,
        4.10560285, -0.63493576,  2.19476774,  0.26573043,  0.27814854,
       -0.37489551,  1.6816916 , -8.73044501, -1.06165042,  7.07193008,
        3.41415783, -0.24936445, -0.26833996, -2.24202593, -0.99458258,
        0.10110003,  0.11960508,  0.30607428, -4.60282134, -1.3357895 ,
       -0.32239014,  6.41540839,  1.0425302 , -0.7250397 , -0.5757551 ,
       -0.51630188,  0.94283431, -1.31457513,  1.94295337, -0.11675262,
        9.91177389,  1.77276456,  0.16492927, -0.74277983,  4.85532393,
        0.23452223, -2.62419515, -9.20112566,  0.33172059,  9.88025346,
        1.19646219,  8.33519835,  7.69753721, -0.41884375, -0.57707577,
        0.82542318, -0.28093189,  0.17848574,  1.31975807,  9.4061475 ,
       -1.20795082,  2.47943756, -0.67523205,  0.83466358, -0.12471565,
       -7.73486289, -0.43588451, -0.42019527, -0.23155583,  0.12387874,
        3.05776202,  0.78676319,  0.13104398, -9.29307184, -2.65354886,
       -1.6797139 ,  0.27418448,  0.59443239, -7.92306001, -1.74983836,
       -0.2025432 ,  0.84682486,  0.28587889,  8.08826701, -2.49036665,
        0.42090131, -0.56237521, -1.13043431,  1.74121992,  3.84392799,
       -3.30216099, -0.18058397,  0.44800833,  1.61757372, -0.12798236,
       -0.9702553 , -0.55651792,  3.92564513,  0.20009299,  0.11969297,
       -8.24112908, -1.06236533,  0.7241885 ,  7.05891655, -8.06906281,
        0.32589925,  2.32943218, -0.64279993, -0.87092519,  0.38868871,
        0.2969108 ,  1.5228902 , -1.05804036, -3.00902999, -0.11394441,
        1.74408244, -0.15009058, -1.09907025, -2.38166399,  0.11891973,
        0.42822813,  4.36744874,  0.16399203,  0.15135633,  0.7570753 ,
       -2.94099909, -2.34601177,  4.90123944, -3.46432078,  0.10265274,
       -0.28261164,  0.56345098, -2.09594134,  0.35437744, -0.32564487,
        0.1127623 , -3.51108834, -0.15157551,  0.1393183 ,  0.34948547,
       -3.5840428 ,  3.31639503, -0.90852028, -3.69718165, -0.49046857,
        6.43488294, -0.13300434,  0.12447419, -0.36601994, -2.38823741,
       -1.35268894, -0.13864249, -0.12676229,  5.82459836,  1.37151347,
        2.21875591, -8.82658645,  4.83645936,  7.16271554,  0.11120619,
       -1.0192601 ,  0.78001651, -0.25414218, -0.20274659, -1.23123889,
        8.22541729,  0.53678049, -5.19283758, -0.37432393, -5.1085179 ,
       -4.42309283,  0.79111053, -6.10884375,  0.95764718, -0.56119905,
       -1.20965608, -2.29043181,  0.46536486,  3.99343621,  3.16356284,
        6.84877709, -2.10841852, -0.14680142, -0.54027868, -1.21782554,
       -0.14526707,  1.32959799, -0.17021787, -1.76575706,  0.28807159,
       -0.75000495,  7.6415549 ,  6.59492243,  4.52541255, -0.78726909,
       -3.98250676, -1.6589023 ,  0.40903186, -2.96111168, -2.28987275,
        0.4722962 , -0.43386637, -0.26553419, -0.74633759,  2.00524351,
        0.99263794,  0.36768645, -0.32648443, -0.84834244,  0.95181881,
        1.73758964, -7.98034072,  3.51406068,  1.25777578, -0.49616287,
       -1.55504479,  0.21046517,  6.03720698, -0.95026296, -0.3454686 ,
       -0.13395231,  0.13628203, -0.65576556,  3.65290027,  2.8395605 ,
       -2.16447004, -1.99604101, -0.14068696, -9.4744051 , -0.56036178,
        0.89263407,  4.73197812, -5.42625507,  0.59510006, -3.19038644,
       -0.1262115 ,  0.58628061, -0.10742226, -0.43617672, -2.46898406,
       -9.03531855, -3.51748178,  0.32693531, -6.16639536, -0.12640255,
        0.37920856,  3.71250125,  0.85851231,  1.06819489, -1.67300003,
        0.82612289, -0.73039715, -3.5756472 ,  1.28300505,  0.13533724,
       -0.39761591,  7.3372453 ,  5.66152488, -2.17737617, -0.10634921,
       -0.26393047,  5.79092816, -7.41643654, -1.57053102, -0.22426296,
        0.28657883, -0.31994904, -0.52829504, -0.1848484 , -5.9998236 ,
        0.23159746,  7.38535428,  1.76000129,  1.97840081,  1.15953415,
        0.44079715, -4.01388227,  8.08467708,  0.13394535,  1.78493112,
        1.73404752,  0.88778669,  9.11043641,  1.11432932, -6.40038305,
       -0.13938686,  6.266873  , -0.26002749,  0.24392412, -0.15392607,
        0.64881252, -0.25621235,  6.25448539,  1.15602716, -0.32056649,
       -0.56833547, -9.71076148,  3.56797199, -8.41171542,  1.74254693,
       -0.68479176, -1.49142937,  3.30956912,  4.40348777, -1.50859856,
       -6.35037505, -0.16205794,  4.89688833, -0.62949167, -0.80140395,
       -0.23986785,  1.49800952, -1.79142261,  0.57020016,  1.00413354,
       -1.70859144, -5.31219649, -0.15290534,  0.50829203,  0.3574686 ,
        1.40172296,  2.59489426,  0.25308043,  2.91388488, -0.15688966,
        0.65462196, -9.63821645,  1.62744149,  0.17346716,  0.14010992,
        0.80524867, -3.24180624,  0.30831111,  8.60372144, -8.38214339,
       -2.51913407,  3.07590665,  1.21908538, -3.3474056 , -0.24552276,
       -4.26677627,  0.36742196,  1.53678249,  0.17418057, -4.09061407,
       -0.2869267 ,  3.3563844 ,  9.75498682,  1.45894226, -1.50369066,
        0.22612725,  0.18695638, -1.29315619, -1.60704945, -0.1859964 ,
       -0.12709088,  4.07240971,  1.03774631, -0.33927721,  0.26877903,
       -0.19848888,  0.2192142 , -0.77317046, -4.39023534,  0.54406971,
       -1.34992354, -0.52128094,  2.84068419,  0.61591964, -3.51988128,
        0.15501359,  9.03294489, -0.79144182,  8.79647008, -8.85482639,
       -8.17408692, -8.84418514,  0.16444876,  1.94611458,  0.13083765,
       -0.15031269,  0.38940629,  0.86330073,  1.0730945 ,  0.16878963,
       -0.50201143, -0.19094163,  2.2323497 ,  0.16195421, -2.45377227,
       -0.2960549 ,  0.16834779,  0.23250438, -0.29076695,  6.4802257 ,
        4.11667997, -6.64943794,  0.10414328, -0.20507128,  0.14890529,
        0.97266858, -0.12350766, -0.14813212,  7.25336711, -1.14207751,
        0.23945036,  6.58812587, -0.54188281, -2.18353167,  0.18527509,
       -5.09093589, -0.4608481 ,  3.17104167,  0.44149924, -0.374161  ,
        0.12474031,  2.50962584, -5.79629127,  4.23865253, -1.55160346,
        1.43960266, -0.29417787,  0.15663056,  9.33624092, -0.45196479,
       -0.60224453,  2.92505815, -0.18340133,  3.12208801,  4.89617204,
        0.39026262,  1.24898628, -0.12066489,  2.77663845,  4.87398081,
        8.54206634, -3.32469848, -0.16678682,  0.12922883,  1.95832391,
        1.95212565, -0.12320786,  1.47110967, -1.37506444,  0.1173145 ,
       -1.66207791, -3.22381293, -0.55204446,  3.14168122,  0.16400014,
       -2.56820562,  0.28444656, -0.8047932 , -0.33247299,  0.31998018,
       -1.5082569 , -1.16954662,  9.73503442,  1.17179613,  0.11448609,
       -0.32897457, -0.12618793,  6.3148249 , -0.12779907, -0.30741862,
        1.78615143, -1.57593396,  1.01425846,  2.09408896,  3.59835956,
        0.43921929,  1.03384552,  0.22336785, -0.5473676 , -2.0023266 ,
        2.8534922 ,  0.34213033,  0.26282579,  0.68083162, -0.96974625,
       -0.13050338, -3.51304861,  0.2526804 , -6.3845605 , -0.37019956,
        1.73906394,  0.25495489,  0.1868707 ,  8.02896348,  0.92420681,
        0.25558651,  1.284741  ,  2.8670148 ,  2.25577408,  0.31908308,
        9.67336376, -2.51483484,  3.53046677, -2.02646227,  1.47588929,
       -4.78622926, -0.23545939, -5.76896406, -0.76556718, -1.22017508,
        1.68903633, -1.7448184 ,  0.5982344 ,  0.57633632, -0.4897347 ,
        0.28559631, -8.74331268, -9.805081  , -5.74073294, -1.05597386]),)
#print(*tupla)
print(fn(*tupla))

[17.69985104 19.8373443  17.51011006 20.11804906 11.49115825 14.58071852
 18.1707416  20.22739928 25.64812422 17.34065903 19.81181773 20.26566017
 17.22576845 20.79565387 26.99852362 27.07256211 18.38415163 24.40375743
 20.25246075 19.10780245 20.27097763 20.69552025 20.17272861 22.24135243
 19.27832651 17.89001191 15.70934477 22.94234569 19.5927508  17.65281685
 19.29122554 20.14558984 16.71301856 24.81205497 23.0003016  18.67818224
 20.492876   25.76599144 21.54445383 27.680522   20.13573639 20.29208526
 28.13640143 18.65622453 20.16257122 19.25015068 20.46854759 19.72947241
 15.69494829 17.96890665 20.20945753 18.09846685 17.10033672 19.02945302
 19.34458685 28.82932876 14.12821818 21.12548343 17.86196048 24.48316936
 19.87868324 21.22905599 18.67289119 19.79116013 21.28852513 11.67290159
 19.31811392 19.3051355  21.88480985 17.96765944 19.1170912  19.72223597
 20.89175362 20.35459854 24.8949342  21.52731261 28.82655668 19.31468008
 20.15189265 19.17280446 20.28255737 17.76258315 20

In [9]:
with open('srsd/medium_set/true_eq/feynman-i.8.14.pkl','rb') as eq:
    equaion=pickle.load(eq)
    print(equaion,type(equaion))

arr=np.loadtxt('srsd/medium_set/test/feynman-i.8.14.txt')
print(arr)
testing=SGA(100,100,0.95,0.3,100,np.array(['x0','x1','x2','x3']),arr,dummy=False)
print('initialized')
testing.initial_population()

testing.fit()

sqrt((x0 - x1)**2 + (x2 - x3)**2) <class 'sympy.core.power.Pow'>
[[ 2.00293401  0.76615789 -1.16301986 -2.29924894  1.67947364]
 [-0.1516021  -0.315528    4.28046425 -0.16175568  4.44524347]
 [ 7.22516759 -0.60686739  5.98877255 -2.48898992 11.54180351]
 ...
 [-0.38752721 -3.80981155 -4.00705763 -9.805081    6.73268929]
 [ 0.15153997  1.39060106 -0.13542526 -5.74073294  5.74062249]
 [-3.96895032 -3.69390316  2.53040955 -1.05597386  3.59691491]]
initialized
pop_created
tan(x2**x3)
sym runtime
cos(sin(x3))
4866089.092567237
cos(x1)**exp(x2)
sym runtime
(5 + pi)**(-x0)


KeyboardInterrupt: 

## Old attempts (with strange problems)

In [113]:
testing=SGA(100,100,0.95,0.3,100,np.array(['x0','x1','x2','x3']),data,dummy=True)
testing.initial_population()
testing.fit()

  1%|          | 1/100 [00:40<1:06:47, 40.48s/it]

exp(x3) 35341.04400568461


  2%|▏         | 2/100 [00:45<31:52, 19.51s/it]  

exp(x3) 35341.04400568461


  3%|▎         | 3/100 [00:54<23:36, 14.61s/it]

...

 99%|█████████▉| 99/100 [24:29<00:29, 29.34s/it]

-2*(x0*tan(4*5))**(1/4) 35340.29096439666


100%|██████████| 100/100 [24:29<00:00, 14.70s/it]

-2*(x0*tan(4*5))**(1/4) 35340.29096439666


ExpNode(kind=np.str_('neg'), num_children=1, children=[ExpNode(kind=np.str_('mul'), num_children=2, children=[array(['2'], dtype='<U2'), ExpNode(kind=np.str_('sqrt'), num_children=1, children=[ExpNode(kind=np.str_('sqrt'), num_children=1, children=[ExpNode(kind=np.str_('mul'), num_children=2, children=[ExpNode(kind=np.str_('tan'), num_children=1, children=[ExpNode(kind=np.str_('mul'), num_children=2, children=[array(['5'], dtype='<U2'), array(['4'], dtype='<U2')], parent=...)], parent=...), array(['x0'], dtype='<U2')], parent=...)], parent=...)], parent=...)], parent=...)], parent=None)

In [116]:
with open('srsd/medium_set/true_eq/feynman-i.8.14.pkl','rb') as eq:
    equaion=pickle.load(eq)
    print(equaion,type(equaion))

arr=np.loadtxt('srsd/medium_set/test/feynman-i.8.14.txt')
print(arr)
testing=SGA(100,100,0.95,0.3,100,np.array(['x0','x1','x2','x3']),arr,dummy=False)
testing.initial_population()
testing.fit()


# print(rng.integers(1,2))
# w=deque()
# w.append('a')
# w.append(17)
# print(w)

sqrt((x0 - x1)**2 + (x2 - x3)**2) <class 'sympy.core.power.Pow'>
[[ 2.00293401  0.76615789 -1.16301986 -2.29924894  1.67947364]
 [-0.1516021  -0.315528    4.28046425 -0.16175568  4.44524347]
 [ 7.22516759 -0.60686739  5.98877255 -2.48898992 11.54180351]
 ...
 [-0.38752721 -3.80981155 -4.00705763 -9.805081    6.73268929]
 [ 0.15153997  1.39060106 -0.13542526 -5.74073294  5.74062249]
 [-3.96895032 -3.69390316  2.53040955 -1.05597386  3.59691491]]


  1%|          | 1/100 [00:17<28:42, 17.40s/it]

exp(pi) 7362.35645742886


  2%|▏         | 2/100 [00:20<14:23,  8.81s/it]

5 - x2 7323.74971794977


...

 99%|█████████▉| 99/100 [02:35<00:01,  1.74s/it]

5 - sin(sin(sin(5 - sin(exp(3) + exp(x0/3))) + cos(x0/3)) + sin(sin(cos(x0/3)))) - sin(sin(sin(sin(cos(3)))) + sin(sin(cos(x0/3)))) - sin(sin(4) + sin(sin(-2 + 5 + sin(sin(cos(x0/3))))) + sin(sin(cos(x0/3)))) - sin(cos(x0/3)) 5200.194624801401


100%|██████████| 100/100 [02:36<00:00,  1.57s/it]

5 - sin(sin(sin(5 - sin(exp(3) + exp(x0/3))) + cos(x0/3)) + sin(sin(cos(x0/3)))) - sin(sin(sin(sin(cos(3)))) + sin(sin(cos(x0/3)))) - sin(sin(4) + sin(sin(-2 + 5 + sin(sin(cos(x0/3))))) + sin(sin(cos(x0/3)))) - sin(cos(x0/3)) 5200.194624801401


5 - sin(sin(sin(5 - sin(exp(3) + exp(x0/3))) + cos(x0/3)) + sin(sin(cos(x0/3)))) - sin(sin(sin(sin(cos(3)))) + sin(sin(cos(x0/3)))) - sin(sin(4) + sin(sin(-2 + 5 + sin(sin(cos(x0/3))))) + sin(sin(cos(x0/3)))) - sin(cos(x0/3))

In [ ]:
#print(type(t[0]))
#sympy.parse_expr('log(x1)/sin(pi)')
#before adding depth regularization
testing=SGA(100,100,0.95,0.3,100,np.array(['x0','x1','x2','x3']),arr,dummy=False)
testing.initial_population()
testing.fit()

  1%|          | 1/100 [00:23<38:55, 23.60s/it]

-sin(x1) 7271.026189509979


  2%|▏         | 2/100 [00:37<29:02, 17.78s/it]

-sin(x1) 7271.026189509979


  3%|▎         | 3/100 [00:40<18:09, 11.23s/it]

...

 99%|█████████▉| 99/100 [04:26<00:08,  8.63s/it]

2 + 3 + sin(2 + 3**(3**(sin(2 + 2**(2*2 + 3**(3**(sin(2 + sin(sqrt(3))**(sqrt(3))/x0)/2 + sin(2 + sin(sqrt(3))**(2 + sin(cos(5)) + sin(sqrt(3))**(2 + 3 + sin(cos(sin(2 + 2/x0))))/x0)/x0)/2)/2 + sin(2 + sin(sqrt(3))**(3**(sin(sqrt(3))/2 + sin(2 + sin(sqrt(3))**(2 + log(sin(3))/sqrt(exp(sqrt(3))))/x0)/2)/x0)/x0)/2)/x0 + x0)/x0)/2 + sin(2 + sin(5**x3)**(2 + 3 + sin(cos(sin(2 + 2/x0))))/x0)/2)/2 + sin(2 + sin(sqrt(3))**(2 + 3 + sin(cos(sin(2 + 2/x0))))/x0)/2)/x0) + sin(2 + 3**(sin(2 + sin(sqrt(3))**(2*2 + sin(2 + 3**(3**(sin(2 + sin(sqrt(3))**(2*2 + x0)/x0)/2 + sin(2 + sin(sqrt(3))**(2 + 3 + sin(cos(5)))/x0)/2)/2 + sin(2 + sin(sqrt(3))**(2 + 3 + sin(cos(sin(2 + 2/x0))))/x0)/2)/x0))/x0)/2 + sin(cos(2 + 2/x0))/2)/x0) 5386.910248857201


100%|██████████| 100/100 [04:35<00:00,  2.76s/it]

2 + 3 + sin(2 + 3**(3**(sin(2 + 2**(2*2 + 3**(3**(sin(2 + sin(sqrt(3))**(sqrt(3))/x0)/2 + sin(2 + sin(sqrt(3))**(2 + sin(cos(5)) + sin(sqrt(3))**(2 + 3 + sin(cos(sin(2 + 2/x0))))/x0)/x0)/2)/2 + sin(2 + sin(sqrt(3))**(3**(sin(sqrt(3))/2 + sin(2 + sin(sqrt(3))**(2 + log(sin(3))/sqrt(exp(sqrt(3))))/x0)/2)/x0)/x0)/2)/x0 + x0)/x0)/2 + sin(2 + sin(5**x3)**(2 + 3 + sin(cos(sin(2 + 2/x0))))/x0)/2)/2 + sin(2 + sin(sqrt(3))**(2 + 3 + sin(cos(sin(2 + 2/x0))))/x0)/2)/x0) + sin(2 + 3**(sin(2 + sin(sqrt(3))**(2*2 + sin(2 + 3**(3**(sin(2 + sin(sqrt(3))**(2*2 + x0)/x0)/2 + sin(2 + sin(sqrt(3))**(2 + 3 + sin(cos(5)))/x0)/2)/2 + sin(2 + sin(sqrt(3))**(2 + 3 + sin(cos(sin(2 + 2/x0))))/x0)/2)/x0))/x0)/2 + sin(cos(2 + 2/x0))/2)/x0) 5386.910248857201


2 + 3 + sin(2 + 3**(3**(sin(2 + 2**(2*2 + 3**(3**(sin(2 + sin(sqrt(3))**(sqrt(3))/x0)/2 + sin(2 + sin(sqrt(3))**(2 + sin(cos(5)) + sin(sqrt(3))**(2 + 3 + sin(cos(sin(2 + 2/x0))))/x0)/x0)/2)/2 + sin(2 + sin(sqrt(3))**(3**(sin(sqrt(3))/2 + sin(2 + sin(sqrt(3))**(2 + log(sin(3))/sqrt(exp(sqrt(3))))/x0)/2)/x0)/x0)/2)/x0 + x0)/x0)/2 + sin(2 + sin(5**x3)**(2 + 3 + sin(cos(sin(2 + 2/x0))))/x0)/2)/2 + sin(2 + sin(sqrt(3))**(2 + 3 + sin(cos(sin(2 + 2/x0))))/x0)/2)/x0) + sin(2 + 3**(sin(2 + sin(sqrt(3))**(2*2 + sin(2 + 3**(3**(sin(2 + sin(sqrt(3))**(2*2 + x0)/x0)/2 + sin(2 + sin(sqrt(3))**(2 + 3 + sin(cos(5)))/x0)/2)/2 + sin(2 + sin(sqrt(3))**(2 + 3 + sin(cos(sin(2 + 2/x0))))/x0)/2)/x0))/x0)/2 + sin(cos(2 + 2/x0))/2)/x0)

In [123]:
testing=SGA(100,100,0.95,0.3,100,np.array(['x0','x1','x2','x3']),arr,dummy=False)
testing.initial_population()
testing.fit()

  1%|          | 1/100 [00:14<23:52, 14.47s/it]

2 + 3 14805.311954711597


  2%|▏         | 2/100 [00:27<22:42, 13.91s/it]

5 + x3 14560.162709228785


  3%|▎         | 3/100 [00:31<14:40,  9.08s/it]

...

 99%|█████████▉| 99/100 [02:28<00:01,  1.45s/it]

5 + cos(4 + 5 + cos(exp(-2 + 4)) - x2/3) + cos(exp(2)) 10806.040167396182


100%|██████████| 100/100 [02:28<00:00,  1.49s/it]

5 + cos(3 + 4) + cos(4 + 5 + cos(exp(2)) - x2/3) 10783.976434999158


5 + cos(3 + 4) + cos(4 + 5 + cos(exp(2)) - x2/3)

In [125]:
testing=SGA(100,100,0.95,0.3,100,np.array(['x0','x1','x2','x3']),arr,dummy=False)
testing.initial_population()
testing.fit()

  1%|          | 1/100 [00:17<29:15, 17.73s/it]

3 + x1 15451.468827629196
[3 + x1, 3 - x1, 2 + x0, (3 + x1)/sqrt(5), 2 - x3, cos(cos(x0)), cos(cos(x1)), cos(cos(x1)), cos(x0), x3]


  2%|▏         | 2/100 [00:30<24:30, 15.01s/it]

3 + x1 15451.468827629196
[3 + x1, 3 - x1, 3 - x3, 2 + x0, (3 + x1)/sqrt(5), (3 + x1)/sqrt(5), 2 - x3, (2 + x1)/sqrt(5), cos(cos(cos(x0))), cos(cos(cos(cos(x1))))]


  3%|▎         | 3/100 [00:32<14:34,  9.02s/it]

...

 99%|█████████▉| 99/100 [02:33<00:01,  1.78s/it]

5 + cos(3 + (-x0 + cos((5 + (-x0 + cos(5))/sqrt(5))/5))/sqrt(5)) + cos(3 + (-x0 + cos(5))/sqrt(5 + cos(cos(5)))) + cos(cos(4/sqrt(5))) 10490.981798177903
[5 + cos(3 + (-x0 + cos((5 + (-x0 + cos(5))/sqrt(5))/5))/sqrt(5)) + cos(3 + (-x0 + cos(5))/sqrt(5 + cos(cos(5)))) + cos(cos(4/sqrt(5))), 5 + cos(5) + cos(3 + (-x0 + cos(5))/sqrt(5)) + cos(3 + (cos(x0) + (-x0 + cos(5))/5**(1/4))/sqrt(5)) + cos(log(2)), 5 + cos(3 + (-x0 + cos(5))/sqrt(5)) + cos(3 + (-x0 + cos((5 + (-x0 + cos(5))/sqrt(5))/5))/sqrt(5)) + cos(cos(4/sqrt(5))), 5 + cos(5 + cos(3 + (3 + x3)/3)) + cos(5 + cos(3 + 2) + cos(3 + x3/sqrt(5 + cos(3 + x3)))), 5 + cos(3 + (-x0 + cos(5))/sqrt(5)) + cos(3 + (cos(5) + (-x0 + cos(5))/sqrt(3 + (cos(5) + (-x0 + cos(5))/sqrt(5))/sqrt(5)))/sqrt(5)) + cos(5 + cos(5)) + cos(log(2)), 5 + cos(5) + cos(3 + (-x0 + cos(5))/sqrt(5)) + cos(3 + (cos(5) + (-x0 + cos(5))/sqrt(3))/sqrt(5)) + cos(log(2)), 5 + cos(5) + cos(3 + (-x0 + cos(5))/sqrt(5)) + cos(3 + (cos(cos(x0)) + (-x0 + cos(5))/sqrt(3 + (cos(5

100%|██████████| 100/100 [02:34<00:00,  1.55s/it]

5 + cos(5) + cos(3 + (-x0 + cos((5 + (-x0 + cos(5))/sqrt(5))/5))/sqrt(5)) + cos(3 + (cos(x0) + (-x0 + cos(5))/5**(1/4))/sqrt(5)) + cos(log(2)) 10486.466698475215
[5 + cos(5) + cos(3 + (-x0 + cos((5 + (-x0 + cos(5))/sqrt(5))/5))/sqrt(5)) + cos(3 + (cos(x0) + (-x0 + cos(5))/5**(1/4))/sqrt(5)) + cos(log(2)), 5 + cos(3 + (-x0 + cos((5 + (-x0 + cos(5))/sqrt(5))/5))/sqrt(5)) + cos(3 + (-x0 + cos(5))/sqrt(5 + cos(cos(5)))) + cos(cos(4/sqrt(5))), 5 + cos(5) + cos(3 + (-x0 + cos(5))/sqrt(5)) + cos(3 + (cos(5) + (-x0 + cos((5 + (-x0 + cos(5))/sqrt(5))/sqrt(5)))/sqrt(3 + (cos(2*x0) + (-5 + cos(5))/sqrt(5))/sqrt(5)))/sqrt(5)) + cos(log(2)), 5 + cos(5) + cos(3 + (-x0 + cos(5))/sqrt(5)) + cos(3 + (cos(x0) + (-x0 + cos(5))/5**(1/4))/sqrt(5)) + cos(log(2)), 5 + cos(3 + (-x0 + cos(5))/sqrt(5)) + cos(3 + (-x0 + cos((5 + (-x0 + cos(5))/sqrt(5))/5))/sqrt(5)) + cos(cos(4/sqrt(5))), 5 + cos(5 + cos(3 + (3 + x3)/3)) + cos(5 + cos(3 + 2) + cos(3 + x3/sqrt(5 + cos(3 + x3)))), 5 + cos(3 + (-x0 + cos(5))/sqrt(5)

5 + cos(5) + cos(3 + (-x0 + cos((5 + (-x0 + cos(5))/sqrt(5))/5))/sqrt(5)) + cos(3 + (cos(x0) + (-x0 + cos(5))/5**(1/4))/sqrt(5)) + cos(log(2))

In [130]:
testing=SGA(100,100,0.95,0.3,100,np.array(['x0','x1','x2','x3']),arr,dummy=False,simplified=True)
testing.initial_population()
testing.fit()

  2%|▏         | 2/100 [00:00<00:10,  9.07it/s]

x1**2 18351.009661017008
[exp(sin(x3)), exp(sin(x3)), cos(cos(x1)), cos(cos(x1)), 1 - cos(x2), sin(cos(cos(x3))), sin(sqrt(exp(x0))), cos(exp(-x1)), sin(exp(x0)), cos(x0)]
exp(cos(x1)) 17140.733225310243
[exp(cos(x1)), exp(sin(x3)), exp(sin(x3)), cos(cos(cos(cos(x1)))), cos(cos(x3)), cos(cos(x1)), cos(cos(x1)), 1 - cos(x2), sin(cos(cos(x3))), sin(cos(cos(x0)))]
exp(cos(x1)) 17140.733225310243
[exp(cos(x1)), exp(cos(x1)), exp(sin(x3)), exp(sin(x3)), exp(sin(x3)), cos(exp(-x1**2)), cos(cos(cos(x3))), cos(cos(cos(cos(x1)))), cos(cos(cos(cos(x1)))), cos(cos(x3))]


  6%|▌         | 6/100 [00:00<00:09,  9.89it/s]

exp(cos(x1)) 17140.733225310243
[exp(cos(x1)), exp(cos(x1)), exp(sin(x3)), exp(sin(x3)), exp(sin(x3)), cos(exp(-x1**2)), cos(cos(cos(x3))), cos(cos(cos(x3))), cos(cos(cos(cos(x1)))), cos(cos(cos(cos(x1))))]
exp(sin(exp(sin(x3)))) 15699.47099184717
[exp(sin(exp(sin(x3)))), exp(cos(x1)), exp(cos(x1)), exp(sin(x3)), exp(sin(x3)), exp(sin(x3)), cos(exp(-x1**2)), cos(exp(-x0**2)), cos(sin(tan(x1))), cos(cos(cos(sin(x2))))]
exp(cos(exp(-x1**2))) 14564.788887425857
[exp(cos(exp(-x1**2))), exp(sin(exp(sin(x1)))), exp(sin(exp(sin(x3)))), exp(exp(sin(x3))), exp(sin(exp(x0))), exp(cos(x1)), exp(cos(x1)), exp(sin(x3)), exp(sin(x3)), exp(sin(x3))]


  8%|▊         | 8/100 [00:00<00:10,  8.81it/s]

...

 99%|█████████▉| 99/100 [00:25<00:00,  3.21it/s]

exp(x0 - x3) 11173.942582830648
[exp(exp(sin(sin(sin(sin(sin(exp(-sin(sin(exp(x3))))))))))), exp(exp(sin(sin(sin(sin(sin(sin(exp(-sin(sin(exp(x3)))))))))))), exp(exp(sin(sin(sin(sin(sin(sin(exp(-sin(sin(exp(x3)))))))))))), exp(exp(sin(sin(sin(sin(sin(sin(exp(-sin(sin(exp(x3)))))))))))), exp(exp(sin(sin(sin(sin(sin(sin(exp(-sin(sin(exp(x3)))))))))))), exp(exp(sin(sin(sin(sin(sin(sin(exp(-sin(sin(exp(x3)))))))))))), exp(exp(sin(sin(sin(sin(sin(sin(exp(-sin(sin(exp(x3)))))))))))), exp(exp(sin(sin(sin(sin(exp(-sin(sin(exp(x3)))))))))), exp(exp(sin(sin(sin(sin(exp(-sin(sin(exp(x3)))))))))), exp(exp(sin(sin(sin(sin(exp(-sin(sin(exp(x3))))))))))]


100%|██████████| 100/100 [00:25<00:00,  3.85it/s]

exp(x0 - x3) 11173.942582830648
[exp(exp(sin(sin(sin(sin(sin(exp(-sin(sin(exp(x3))))))))))), exp(exp(sin(sin(sin(sin(sin(exp(-sin(sin(exp(x3))))))))))), exp(exp(sin(sin(sin(sin(sin(sin(exp(-sin(sin(exp(x3)))))))))))), exp(exp(sin(sin(sin(sin(sin(sin(exp(-sin(sin(exp(x3)))))))))))), exp(exp(sin(sin(sin(sin(sin(sin(exp(-sin(sin(exp(x3)))))))))))), exp(exp(sin(sin(sin(sin(sin(sin(exp(-sin(sin(exp(x3)))))))))))), exp(exp(sin(sin(sin(sin(sin(sin(exp(-sin(sin(exp(x3)))))))))))), exp(exp(sin(sin(sin(sin(sin(sin(exp(-sin(sin(exp(x3)))))))))))), exp(exp(sin(sin(sin(sin(exp(-sin(sin(exp(x3)))))))))), exp(exp(sin(sin(sin(sin(exp(-sin(sin(exp(x3))))))))))]


exp(x0 - x3)

In [131]:
testing=SGA(100,100,0.95,0.3,100,np.array(['x0','x1','x2','x3']),data,dummy=True,simplified=True)
testing.initial_population()
testing.fit()

  2%|▏         | 2/100 [00:00<00:12,  8.03it/s]

sqrt(x1**x1) 35341.04400593562
[-x0, -x0, log(cos(x0)), tan(x0), tan(x0), tan(x0), sin(x0), tan(x0), sin(sqrt(x0)), sqrt(x0)]
sqrt(x1**x1) 35341.04400593562
[-x0, -x0, -x0, -x0, -x0, log(cos(x0)), x0**2, tan(x0), tan(x0), tan(x0)]


  4%|▍         | 4/100 [00:00<00:12,  7.39it/s]

sqrt(x1**x1) 35341.04400593562
[-x0, -x0, -x0, -x0, -x0, -x0, -x0, log(cos(x0)), x0**2, x0**2]
sqrt(x1**x1) 35341.04400593562
[-x0, -x0, -x0, -x0, -x0, -x0, -x0, -x0, -x0, -x0]


  6%|▌         | 6/100 [00:00<00:11,  7.90it/s]

...

 99%|█████████▉| 99/100 [00:18<00:00,  4.29it/s]

-sqrt(6*sqrt(x0) - 2*x0) 35340.29097856337
[-sqrt(6*sqrt(x0) - 2*x0), -sqrt(6*sqrt(x0) - 2*x0), -sqrt(6*sqrt(x0) - 2*x0), -sqrt(6*sqrt(x0) - 2*x0), -sqrt(6*sqrt(x0) - 2*x0), -sqrt(6*sqrt(x0) - 2*x0), -sqrt(6*sqrt(x0) - 2*x0), -sqrt(6*sqrt(x0) - 2*x0), -sqrt(6*sqrt(x0) - 2*x0), -sqrt(6*sqrt(x0) - 2*x0)]


100%|██████████| 100/100 [00:18<00:00,  5.35it/s]

-sqrt(6*sqrt(x0) - 2*x0) 35340.29097856337
[-sqrt(6*sqrt(x0) - 2*x0), -sqrt(6*sqrt(x0) - 2*x0), -sqrt(6*sqrt(x0) - 2*x0), -sqrt(6*sqrt(x0) - 2*x0), -sqrt(6*sqrt(x0) - 2*x0), -sqrt(6*sqrt(x0) - 2*x0), -sqrt(6*sqrt(x0) - 2*x0), -sqrt(6*sqrt(x0) - 2*x0), -sqrt(6*sqrt(x0) - 2*x0), -sqrt(6*sqrt(x0) - 2*x0)]


-sqrt(6*sqrt(x0) - 2*x0)